**Aim: To recommend products that have been most commonly brought along with the product purchased by the customer**

In [0]:
#from google.colab import drive
#drive.mount('/content/drive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
#!wget https://he-s3.s3.amazonaws.com/media/hackathon/future-datathon-1/clustering-customers/72cb9080-b-Q1ClData.zip

--2018-11-25 10:03:11--  https://he-s3.s3.amazonaws.com/media/hackathon/future-datathon-1/clustering-customers/72cb9080-b-Q1ClData.zip
Resolving he-s3.s3.amazonaws.com (he-s3.s3.amazonaws.com)... 52.219.40.128
Connecting to he-s3.s3.amazonaws.com (he-s3.s3.amazonaws.com)|52.219.40.128|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 2954247 (2.8M) [application/zip]
Saving to: ‘72cb9080-b-Q1ClData.zip.1’

72cb9080-b-Q1ClData 100%[===================>]   2.82M  2.60MB/s    in 1.1s    

2018-11-25 10:03:13 (2.60 MB/s) - ‘72cb9080-b-Q1ClData.zip.1’ saved [2954247/2954247]



In [1]:
from google.colab import files
files.upload()

Saving cproducts.csv to cproducts.csv
Saving sampleSubmission.csv to sampleSubmission.csv


{'cproducts.csv': b'customerID,DOB,Gender,State,PinCode,transactionDate,store_code,store_description,till_no,transaction_number_by_till,promo_code,promotion_description,product_code,product_description,sale_price_after_promo,discountUsed\nBBID_20482,1975-10-20,male,MADHYA PRADESH,453441,2016-05-01,2655,BB-INDORE-MALHAR MEGA MALL,2,85246,NONPROMO,,1000446431,PATANJALI CHOCOS 125g,55,Payback\nBBID_20485,1955-07-21,female,,999999,2017-03-09,2655,BB-INDORE-MALHAR MEGA MALL,8,78829,NONPROMO,,1000010431,SOO FRESH ROLLS HOT DOG 4P,30,Payback\nBBID_20498,1981-03-19,female,MAHARASHTRA,400064,2015-08-12,2655,BB-INDORE-MALHAR MEGA MALL,13,1064,0000971754,AD 399 FLAT LADIES JEANS  FASHION EXC,1000077851005,"DLJ-0010-BSF-2-CJ-FL, 34, BLACK",418.95,Payback\nBBID_20499,1986-05-10,male,MAHARASHTRA,400099,2016-12-18,2615,BB-AMRITSAR-TRILIUM MALL,14,51080,NONPROMO,,1000443231,PATANJALI TOMATO KETCHUP BT 500g,70,Payback\nBBID_204110,1988-02-29,male,MADHYA PRADESH,474001,2015-12-31,2655,BB-INDORE-MALHAR M

In [0]:
## load libraries
import pandas as pd
import numpy as np
from sklearn.preprocessing import LabelEncoder
import scipy.sparse as sps
import warnings
warnings.filterwarnings('ignore')
from tqdm import tqdm

In [0]:
# load product and sample file
products = pd.read_csv('cproducts.csv')

In [0]:
sample = pd.read_csv('sampleSubmission.csv')

In [6]:
sample.head()

customerID                                           products
0  BBID_204221  300663432,1000099534,1000475598,None,None,None...
1  BBID_204254  300663432,1000099534,1000475598,None,None,None...
2  BBID_204830  300663432,1000099534,1000475598,None,None,None...
3  BBID_204880  300663432,1000099534,1000475598,None,None,None...
4  BBID_204910  300663432,1000099534,1000475598,None,None,None...

In [7]:
'BBID_20410043' in sample['customerID']

False

In [8]:
## number of unique customers
products['customerID'].nunique()

10410

In [0]:

products['transactionDate'] = pd.to_datetime(products['transactionDate'])
mask = (products['transactionDate'] >= '2016-12-01')
products = products.loc[mask]

In [0]:
products.sort_values('transactionDate',inplace=True)
products = products.reset_index(drop=True)

In [11]:
products.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4381 entries, 0 to 4380
Data columns (total 16 columns):
customerID                    4381 non-null object
DOB                           4273 non-null object
Gender                        4099 non-null object
State                         3996 non-null object
PinCode                       4201 non-null float64
transactionDate               4381 non-null datetime64[ns]
store_code                    4381 non-null int64
store_description             4381 non-null object
till_no                       4381 non-null int64
transaction_number_by_till    4381 non-null int64
promo_code                    4381 non-null object
promotion_description         1449 non-null object
product_code                  4381 non-null int64
product_description           4381 non-null object
sale_price_after_promo        4381 non-null float64
discountUsed                  4381 non-null object
dtypes: datetime64[ns](1), float64(2), int64(4), object(9)
memory usage

In [0]:
## take only those customers which are in sample submission file
products_2 = products[products['customerID'].isin(sample['customerID'])]

## remove missing values # 4
products_2 = products_2[~pd.isnull(products_2['product_code'])]

## convert type of product code
products_2['product_code'] = products_2['product_code'].astype(np.int64)

In [0]:
products_2 = products_2.loc[:,['customerID','product_code']]
products_2 = products_2.reset_index(drop=True)

In [14]:
products_2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2029 entries, 0 to 2028
Data columns (total 2 columns):
customerID      2029 non-null object
product_code    2029 non-null int64
dtypes: int64(1), object(1)
memory usage: 31.8+ KB


In [0]:
## these customers are not in train, so we'll predict None for them at last
misfit_customers = list(set(sample['customerID']) - set(products_2['customerID']))

In [0]:
## create product list by customers
products_2 = products_2.groupby('customerID')['product_code'].apply(lambda x: x.tolist()).reset_index()

In [0]:
## remove duplicate products
products_2['product_code'] = products_2['product_code'].map(lambda x: list(set(x)))

In [18]:
products_2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1847 entries, 0 to 1846
Data columns (total 2 columns):
customerID      1847 non-null object
product_code    1847 non-null object
dtypes: object(2)
memory usage: 28.9+ KB


In [0]:
## fix product max len to 20 (we'll pick the last 20 i.e most recent ones)
products_2['product_code'] = products_2['product_code'].map(lambda x: x[-20:])

In [20]:
products_2.head()

customerID  product_code
0  BBID_20410014   [108100331]
1  BBID_20410046   [108027409]
2  BBID_20410083  [1000598648]
3   BBID_2041010  [1000109366]
4  BBID_20410211   [108100319]

In [0]:
### create a list of customers & products

customerIDs = []
product_codes = []

for index, row in products_2.iterrows():
    #if index % 10 == 0:
    #    print (index)
    ls_len = len(row['product_code'])
    customerIDs.extend(np.repeat(row['customerID'], ls_len))
    product_codes.extend(row['product_code'])

In [0]:
## encode values 

from sklearn.preprocessing import LabelEncoder

lbl = LabelEncoder() ## for customers
customerIDs = lbl.fit_transform(customerIDs)
 
lbl2 = LabelEncoder() ## for products
product_codes = lbl2.fit_transform(product_codes)

In [0]:
n_unique_users = len(set(customerIDs))
n_unique_products = len(set(product_codes))

row = customerIDs
col = product_codes

vals = np.repeat(1, len(row))

## this matrix has information about a user bought which all products.
user_product_matrix = sps.csr_matrix((vals, (row, col)), shape=(n_unique_users, n_unique_products))

## this matrix has information a product got bought along with which other products, and how many times
product_cooccurence_matrix = (user_product_matrix.T * user_product_matrix)

## set diagonal equals to zero since we are not interested in knowing the count of a product with itself
product_cooccurence_matrix.setdiag(np.repeat(0, product_cooccurence_matrix.shape[0]))

In [0]:
## create a data frame of encoded values
product_summary = pd.DataFrame({'customerID':customerIDs, 'product_code':product_codes})
product_summary = product_summary.groupby('customerID')['product_code'].agg(lambda x:x.tolist()).reset_index().rename(columns = {0:'product_collection'})

In [0]:
## how many recommendation to make
def take_top_(x):
    if x >= 20:
        return 1
    else:
        if x < 20:
            return int(np.round(20/x))
        
## get count of products per customer
product_summary['len_collection'] = product_summary['product_collection'].map(len)

## if a customer has 20 products in the list, we'll take 1 top most product per each product
product_summary['take_top'] = product_summary['len_collection'].map(lambda x: take_top_(x))

In [0]:
## recommendation function
def recommend_affinity(user):
    
    products_ = product_summary[product_summary['customerID'] == user]['product_collection'].iloc[0] # returns list
    take_top_ = product_summary[product_summary['customerID'] == user]['take_top'].iloc[0]
    
    recs = []
    
    if take_top_ == 0:
        return recs
    
    ## here we get the list of products which were bought the maximum number of times along with a particular productr
    for tt in products_:
        s = np.squeeze(np.asarray(product_cooccurence_matrix[tt].todense())) ## list of products bought with counts` with that product
        ll = s.argsort()[-int(take_top_):][::-1]
        recs.append(list(ll))

    recs = list(np.vstack(recs).flatten('F'))
 
    if not recs:
        return recs
    
    return recs

In [0]:
## recommendation for customers
unique_customers = []

for i in sample['customerID']:
    if i not in misfit_customers:
        unique_customers.append(i)

unique_customers = lbl.fit_transform(unique_customers)

In [28]:
from collections import defaultdict
out_dict = defaultdict(list)

nulls = []

for user in tqdm(unique_customers): #[:50]): ## i took first 50 customers. 
    rec = recommend_affinity(user)
    if not rec:
        nulls.append(user)
    out_dict[user] = rec
#    if i% 10 == 0:
#         print(i)

100%|██████████| 1847/1847 [00:03<00:00, 576.71it/s]


In [0]:
## get unique items per customer
from collections import defaultdict

out_dict_2 = defaultdict(list)

for k,v in out_dict.items():
    out_dict_2[k] = list(set(v))

In [0]:
## convert key values to inverse customer codes

customer_codes = list(lbl.inverse_transform(customerIDs))
customer_maps = dict(zip(list(customerIDs), list(customer_codes)))

In [0]:
out_dict_3 = defaultdict(list)

for k,v in out_dict_2.items():
    out_dict_3[customer_maps[k]] = out_dict_2[k]

In [0]:
mis_dict = defaultdict(list)

for i in misfit_customers:
    mis_dict[i] = list(np.repeat('None', 20))

In [0]:
out_dict_3.update(mis_dict)

In [0]:
submission = pd.DataFrame(list(out_dict_3.items()), columns=['customerID','products'])

In [35]:
submission.head()

customerID                                           products
0   BBID_204910  [480, 481, 482, 483, 484, 485, 486, 487, 488, ...
1  BBID_2043667  [480, 289, 994, 481, 482, 483, 294, 486, 484, ...
2  BBID_2044951  [480, 481, 482, 483, 484, 485, 486, 487, 488, ...
3  BBID_2046414  [480, 353, 33, 483, 484, 485, 358, 481, 488, 4...
4  BBID_2049817  [480, 481, 482, 483, 484, 485, 486, 487, 488, ...

In [0]:

product_codes_inv = list(lbl2.inverse_transform(product_codes))
product_maps = dict(zip(list(product_codes), list(product_codes_inv)))

In [0]:
submission['products'] = submission['products'].map(lambda x: [product_maps.get(s) for s in x])

In [0]:
for index, row in submission.iterrows():
    max_len = 20
    if len(row['products']) < max_len:
        size = len(row['products'])
        diff_ = max_len - size
        a = row['products']
        a.extend(np.repeat('None', diff_))
        submission.loc[index, 'products'] = a
    else:
        submission.loc[index, 'products'] = row['products'][:20]

In [0]:
submission['products'] = submission['products'].map(lambda x: ','.join(str(e) for e in x))

In [40]:
submission.head()

customerID                                           products
0   BBID_204910  300165587,300168306,300170859,300171566,300174...
1  BBID_2043667  300165587,108030061,1000196248,300168306,30017...
2  BBID_2044951  300165587,300168306,300170859,300171566,300174...
3  BBID_2046414  300165587,108100137,108000593,300171566,300174...
4  BBID_2049817  300165587,300168306,300170859,300171566,300174...

In [0]:
submission.to_csv('recommended.csv', index=False)